### Installing the required libraries for the system.

In [2]:
!pip install coloredlogs  --quiet
!pip install yfinance --quiet

### StockData Class is implemented for downloading real-time stocks data with the help of Yahoo Finance API. The Class is initialized with some parameters :     

1.   STOCK = "AAPL"
2.   START = "2018-08-11" (Date in the format of yyyy-mm-dd)
3.   END = "2019-08-11" (Date in the format of yyyy-mm-dd)
4.   FILE_NAME = "{}-{}.csv".format(STOCK, END)
5.   VERBOSE = -2 (Keyword Argument)
6.   NUM_SAMPLES = 15 (Keyword Argument)
7.   ENCODING = "utf-8" (Keyword Argument)

In [ ]:
import pandas as pd
import numpy as np
import yfinance as yf

class StockData :
    def __init__(self, name_of_stock, start_date, end_date, data_type="csv") :
        super(StockData, self).__init__()
        self. name_of_stock = name_of_stock
        self.start_date = start_date
        self.end_date = end_date
        self.data_type = data_type

    def getStockDataToCSV(self, **kwargs) :
        if self.data_type == "csv" :
            stock_data = yf.download(self.name_of_stock, start=self.start_date, end=self.end_date)
            if kwargs["verbose"] > -1 : 
                print("{}The Data is : {}".format("\n", "\n"))
                print(stock_data.head(kwargs["num_samples"]))
            result = stock_data.to_csv(kwargs["file_name"], encoding=kwargs["file_encoding"], index=True)
            return True
        else :
            print("Only CSV file is supported, change the data_type....")
            return False


if __name__ == "__main__" :
    STOCK = "AAPL"
    START = "2018-08-11" # Date in the format of yyyy-mm-dd
    END = "2019-08-11" # Date in the format of yyyy-mm-dd
    FILE_NAME = "{}-{}.csv".format(STOCK, END)
    VERBOSE = -2
    NUM_SAMPLES = 15
    ENCODING = "utf-8"

    stock = StockData(STOCK, START, END)
    result = stock.getStockDataToCSV(num_samples=NUM_SAMPLES, 
                                     verbose=VERBOSE, 
                                     file_name=FILE_NAME, 
                                     file_encoding=ENCODING)
    if result :
        print("Data Generated Successfully....")
    else :
        print("Internal Exception occured try again....")
        print("Try again....")


In [3]:
import os
import math
import random
import logging
import numpy as np
import pandas as pd
import tensorflow as tf
import keras.backend as K
from tqdm import tqdm
from collections import deque
from keras.models import Sequential
from keras.layers import Dense, LeakyReLU
from keras.optimizers import Adam
from keras.models import load_model, clone_model
import coloredlogs
import warnings
warnings.filterwarnings("ignore")


def huber_loss(y_true, y_pred, clip_delta=1.0):
    """Huber loss - Custom Loss Function for Q Learning"""
    error = y_true - y_pred
    cond = K.abs(error) <= clip_delta
    squared_loss = 0.5 * K.square(error)
    quadratic_loss = 0.5 * K.square(clip_delta) + clip_delta * (K.abs(error) - clip_delta)
    return K.mean(tf.where(cond, squared_loss, quadratic_loss))


class Agent:
    """ Stock Trading Bot """
    def __init__(self, state_size, strategy="t-dqn", reset_every=1000, pretrained=False, model_name=None):
        self.strategy = strategy

        # agent config
        self.state_size = state_size    	# normalized previous days
        self.action_size = 3           		# [sit, buy, sell]
        self.model_name = model_name
        self.inventory = []
        self.memory = deque(maxlen=10000)
        self.first_iter = True

        # model config
        self.model_name = model_name
        self.gamma = 0.95 # affinity for long term reward
        self.epsilon = 1.0
        self.epsilon_min = 0.01
        self.beta_1 = 0.99
        self.beta_2 = 0.89
        self.epsilon_decay = 0.995
        self.learning_rate = 0.001
        self.loss = huber_loss
        self.custom_objects = {"huber_loss": huber_loss}  # important for loading the model from memory
        self.optimizer = Adam(learning_rate=self.learning_rate, beta_1=self.beta_1, beta_2=self.beta_2)

        if pretrained and self.model_name is not None:
            self.model = self.load()
        else:
            self.model = self._model()

        # strategy config
        if self.strategy in ["t-dqn", "double-dqn"]:
            self.n_iter = 1
            self.reset_every = reset_every

            # target network
            self.target_model = clone_model(self.model)
            self.target_model.set_weights(self.model.get_weights())

    def _model(self):
        """Creates the model
        """
        model = Sequential()
        model.add(Dense(units=128, activation="relu", input_dim=self.state_size))
        model.add(tf.keras.layers.Dropout(0.1))
        model.add(tf.keras.layers.BatchNormalization())
        model.add(LeakyReLU(alpha=0.27))

        model.add(Dense(units=256, activation="relu"))
        model.add(tf.keras.layers.Dropout(0.15))
        model.add(tf.keras.layers.BatchNormalization())
        model.add(LeakyReLU(alpha=0.27))

        model.add(Dense(units=256, activation="relu"))
        model.add(tf.keras.layers.Dropout(0.15))
        model.add(tf.keras.layers.BatchNormalization())
        model.add(LeakyReLU(alpha=0.27))

        model.add(Dense(units=128, activation="relu"))
        model.add(tf.keras.layers.Dropout(0.15))
        model.add(tf.keras.layers.BatchNormalization())
        model.add(LeakyReLU(alpha=0.27))
        
        model.add(Dense(units=self.action_size))
        model.compile(loss=self.loss, optimizer=self.optimizer)
        return model

    def remember(self, state, action, reward, next_state, done):
        """Adds relevant data to memory
        """
        self.memory.append((state, action, reward, next_state, done))

    def act(self, state, is_eval=False):
        """Take action from given possible set of actions
        """
        # take random action in order to diversify experience at the beginning
        if not is_eval and random.random() <= self.epsilon:
            return random.randrange(self.action_size)

        if self.first_iter:
            self.first_iter = False
            return 1 # make a definite buy on the first iter

        action_probs = self.model.predict(state)
        return np.argmax(action_probs[0])

    def train_experience_replay(self, batch_size):
        """Train on previous experiences in memory
        """
        mini_batch = random.sample(self.memory, batch_size)
        X_train, y_train = [], []
        
        # DQN
        if self.strategy == "dqn":
            for state, action, reward, next_state, done in mini_batch:
                if done:
                    target = reward
                else:
                    # approximate deep q-learning equation
                    target = reward + self.gamma * np.amax(self.model.predict(next_state)[0])

                # estimate q-values based on current state
                q_values = self.model.predict(state)
                # update the target for current action based on discounted reward
                q_values[0][action] = target

                X_train.append(state[0])
                y_train.append(q_values[0])

        # DQN with fixed targets
        elif self.strategy == "t-dqn":
            if self.n_iter % self.reset_every == 0:
                # reset target model weights
                self.target_model.set_weights(self.model.get_weights())

            for state, action, reward, next_state, done in mini_batch:
                if done:
                    target = reward
                else:
                    # approximate deep q-learning equation with fixed targets
                    target = reward + self.gamma * np.amax(self.target_model.predict(next_state)[0])

                # estimate q-values based on current state
                q_values = self.model.predict(state)
                # update the target for current action based on discounted reward
                q_values[0][action] = target

                X_train.append(state[0])
                y_train.append(q_values[0])

        # Double DQN
        elif self.strategy == "double-dqn":
            if self.n_iter % self.reset_every == 0:
                # reset target model weights
                self.target_model.set_weights(self.model.get_weights())

            for state, action, reward, next_state, done in mini_batch:
                if done:
                    target = reward
                else:
                    # approximate double deep q-learning equation
                    target = reward + self.gamma * self.target_model.predict(next_state)[0][np.argmax(self.model.predict(next_state)[0])]

                # estimate q-values based on current state
                q_values = self.model.predict(state)
                # update the target for current action based on discounted reward
                q_values[0][action] = target

                X_train.append(state[0])
                y_train.append(q_values[0])
                
        else:
            raise NotImplementedError()

        # update q-function parameters based on huber loss gradient
        loss = self.model.fit(np.array(X_train), np.array(y_train),epochs=1, verbose=0).history["loss"][0]
        # as the training goes on we want the agent to
        # make less random and more optimal decisions
        if self.epsilon > self.epsilon_min:
            self.epsilon *= self.epsilon_decay

        return loss

    def save(self, episode):
        self.model.save("models/{}_{}".format(self.model_name, episode))

    def load(self):
        return load_model("models/" + self.model_name, custom_objects=self.custom_objects)


def sigmoid(x):
    """Performs sigmoid operation
    """
    try:
        if x < 0:
            return 1 - 1 / (1 + math.exp(x))
        return 1 / (1 + math.exp(-x))
    except Exception as err:
        print("Error in sigmoid: " + err)


def get_state(data, t, n_days):
    """Returns an n-day state representation ending at time t
    """
    d = t - n_days + 1
    block = data[d: t + 1] if d >= 0 else -d * [data[0]] + data[0: t + 1]  # pad with t0
    res = []
    for i in range(n_days - 1):
        res.append(sigmoid(block[i + 1] - block[i]))
    return np.array([res])



In [4]:
# Formats Position
format_position = lambda price: ('-$' if price < 0 else '+$') + '{0:.2f}'.format(abs(price))

# Formats Currency
format_currency = lambda price: '${0:.2f}'.format(abs(price))


def show_train_result(result, val_position, initial_offset):
    """ Displays training results
    """
    if val_position == initial_offset or val_position == 0.0:
        logging.info('Episode {}/{} - Train Position: {}  Val Position: USELESS  Train Loss: {:.4f}'
                     .format(result[0], result[1], format_position(result[2]), result[3]))
    else:
        logging.info('Episode {}/{} - Train Position: {}  Val Position: {}  Train Loss: {:.4f})'
                     .format(result[0], result[1], format_position(result[2]), format_position(val_position), result[3],))


def show_eval_result(model_name, profit, initial_offset):
    """ Displays eval results
    """
    if profit == initial_offset or profit == 0.0:
        logging.info('{}: USELESS\n'.format(model_name))
    else:
        logging.info('{}: {}\n'.format(model_name, format_position(profit)))


def get_stock_data(stock_file):
    """Reads stock data from csv file
    """
    df = pd.read_csv(stock_file)
    return list(df['Adj Close'])


def switch_k_backend_device():
    """ Switches `keras` backend from GPU to CPU if required.
    Faster computation on CPU (if using tensorflow-gpu).
    """
    if K.backend() == "tensorflow":
        logging.debug("switching to TensorFlow for CPU")
        os.environ["CUDA_VISIBLE_DEVICES"] = "-1"


In [5]:
def train_model(agent, episode, data, ep_count=100, batch_size=32, window_size=10):
    total_profit = 0
    data_length = len(data) - 1

    agent.inventory = []
    avg_loss = []

    state = get_state(data, 0, window_size + 1)

    for t in tqdm(range(data_length), total=data_length, leave=True, desc='Episode {}/{}'.format(episode, ep_count)):        
        reward = 0
        next_state = get_state(data, t + 1, window_size + 1)

        # select an action
        action = agent.act(state)

        # BUY
        if action == 1:
            agent.inventory.append(data[t])

        # SELL
        elif action == 2 and len(agent.inventory) > 0:
            bought_price = agent.inventory.pop(0)
            delta = data[t] - bought_price
            reward = delta #max(delta, 0)
            total_profit += delta

        # HOLD
        else:
            pass

        done = (t == data_length - 1)
        agent.remember(state, action, reward, next_state, done)

        if len(agent.memory) > batch_size:
            loss = agent.train_experience_replay(batch_size)
            avg_loss.append(loss)

        state = next_state

    if episode % 10 == 0:
        agent.save(episode)

    return (episode, ep_count, total_profit, np.mean(np.array(avg_loss)))


def evaluate_model(agent, data, window_size, debug):
    total_profit = 0
    data_length = len(data) - 1

    history = []
    agent.inventory = []
    
    state = get_state(data, 0, window_size + 1)

    for t in range(data_length):        
        reward = 0
        next_state = get_state(data, t + 1, window_size + 1)
        
        # select an action
        action = agent.act(state, is_eval=True)

        # BUY
        if action == 1:
            agent.inventory.append(data[t])

            history.append((data[t], "BUY"))
            if debug:
                logging.debug("Buy at: {}".format(format_currency(data[t])))
        
        # SELL
        elif action == 2 and len(agent.inventory) > 0:
            bought_price = agent.inventory.pop(0)
            delta = data[t] - bought_price
            reward = delta #max(delta, 0)
            total_profit += delta

            history.append((data[t], "SELL"))
            if debug:
                logging.debug("Sell at: {} | Position: {}".format(
                    format_currency(data[t]), format_position(data[t] - bought_price)))
        # HOLD
        else:
            history.append((data[t], "HOLD"))

        done = (t == data_length - 1)
        agent.memory.append((state, action, reward, next_state, done))

        state = next_state
        if done:
            return total_profit, history


In [ ]:

def main(train_stock, val_stock, window_size, batch_size, ep_count,
         strategy="t-dqn", model_name="model_debug", pretrained=False, debug=False):
    """ Trains the stock trading bot using Deep Q-Learning."""

    agent = Agent(window_size, strategy=strategy, pretrained=pretrained, model_name=model_name)
    
    train_data = get_stock_data(train_stock)
    val_data = get_stock_data(val_stock)

    initial_offset = val_data[1] - val_data[0]

    for episode in range(1, ep_count + 1):
        train_result = train_model(agent, episode, train_data, ep_count=ep_count,
                                   batch_size=batch_size, window_size=window_size)
        val_result, _ = evaluate_model(agent, val_data, window_size, debug)
        show_train_result(train_result, val_result, initial_offset)


if __name__ == "__main__":
    
    train_stock = "/content/Stock-Data/AAPL.csv"
    val_stock = "/content/Stock-Data/AAPL_2018.csv"
    strategy = "t-dqn"
    window_size = 35
    batch_size = 128
    ep_count = 2
    model_name = "model_debug"
    pretrained = False
    debug = False

    coloredlogs.install(level="DEBUG")
    switch_k_backend_device()

    try:
        main(train_stock, 
             val_stock, 
             window_size, 
             batch_size,
             ep_count, 
             strategy=strategy, 
             model_name=model_name, 
             pretrained=pretrained, 
             debug=debug)
        
    except KeyboardInterrupt:
        print("Aborted!")


2023-01-13 05:16:16 7adabc8c9b2d root[820] DEBUG switching to TensorFlow for CPU
Episode 1/2:   0%|          | 0/1760 [00:00<?, ?it/s]

1/1 [==============================] - 0s 14ms/step


Episode 1/2:   7%|▋         | 129/1760 [00:11<02:31, 10.79it/s]

1/1 [==============================] - 0s 14ms/step


Episode 1/2:   7%|▋         | 129/1760 [00:30<02:31, 10.79it/s]

...

1/1 [==============================] - 0s 14ms/step


Episode 1/2:  20%|██        | 356/1760 [41:34<4:13:10, 10.82s/it]

1/1 [==============================] - 0s 15ms/step


Episode 1/2:  20%|██        | 357/1760 [41:45<4:12:57, 10.82s/it]

1/1 [==============================] - ETA: 0s

In [ ]:
import os
import coloredlogs
from docopt import docopt


def main(eval_stock, window_size, model_name, debug):
    """ Evaluates the stock trading bot.
    """    
    data = get_stock_data(eval_stock)
    initial_offset = data[1] - data[0]

    # Single Model Evaluation
    if model_name is not None:
        agent = Agent(window_size, pretrained=True, model_name=model_name)
        profit, _ = evaluate_model(agent, data, window_size, debug)
        show_eval_result(model_name, profit, initial_offset)
        
    # Multiple Model Evaluation
    else:
        for model in os.listdir("/content/models"):
            if os.path.isfile(os.path.join("/content/models", model)):
                agent = Agent(window_size, pretrained=True, model_name=model)
                profit = evaluate_model(agent, data, window_size, debug)
                show_eval_result(model, profit, initial_offset)
                del agent


if __name__ == "__main__":

    eval_stock = "/content/GOOG_2019.csv" # Evaluation Stock Sheet
    window_size = 10
    model_name = "model_dqn_GOOG_50" # Create a models folder in the runtime and place the trained models
    debug = True

    coloredlogs.install(level="DEBUG")
    switch_k_backend_device()

    try:
        main(eval_stock, window_size, model_name, debug)
    except KeyboardInterrupt:
        print("Aborted")


2023-01-11 13:04:23 5dffcc0e29d7 root[1464] DEBUG switching to TensorFlow for CPU
2023-01-11 13:04:23 5dffcc0e29d7 root[1464] DEBUG Buy at: $1045.85


1/1 [==============================] - 0s 48ms/step


2023-01-11 13:04:23 5dffcc0e29d7 root[1464] DEBUG Sell at: $1016.06 | Position: -$29.79


1/1 [==============================] - 0s 13ms/step


2023-01-11 13:04:23 5dffcc0e29d7 root[1464] DEBUG Buy at: $1057.19


...

2023-01-11 13:04:32 5dffcc0e29d7 root[1464] DEBUG Buy at: $1348.84


1/1 [==============================] - 0s 12ms/step


2023-01-11 13:04:32 5dffcc0e29d7 root[1464] DEBUG Sell at: $1343.56 | Position: -$5.28


1/1 [==============================] - 0s 12ms/step


2023-01-11 13:04:32 5dffcc0e29d7 root[1464] INFO model_dqn_GOOG_50: +$1111.66



## Visualization of the prediction

In [ ]:
!pip install altair --quiet

In [ ]:
import pandas as pd
import numpy as np

import altair as alt
import seaborn as sns

In [ ]:
model_name = 'model_t-dqn_GOOG_10'
test_stock = '/content/GOOG_2019.csv'
window_size = 10
debug = True

agent = Agent(window_size, pretrained=True, model_name=model_name)

In [ ]:
# read csv into dataframe
df = pd.read_csv(test_stock)
# filter out the desired features
df = df[['Date', 'Adj Close']]
# rename feature column names
df = df.rename(columns={'Adj Close': 'actual', 'Date': 'date'})
# convert dates from object to DateTime type
dates = df['date']
dates = pd.to_datetime(dates, infer_datetime_format=True)
df['date'] = dates

df.head()

In [ ]:
import logging
import coloredlogs

coloredlogs.install(level='DEBUG')
switch_k_backend_device()

test_data = get_stock_data(test_stock)
initial_offset = test_data[1] - test_data[0]

test_result, history = evaluate_model(agent, test_data, window_size, debug)

show_eval_result(model_name, test_result, initial_offset)

In [ ]:
def visualize(df, history, title="trading session"):
    # add history to dataframe
    position = [history[0][0]] + [x[0] for x in history]
    actions = ['HOLD'] + [x[1] for x in history]
    df['position'] = position
    df['action'] = actions
    
    # specify y-axis scale for stock prices
    scale = alt.Scale(domain=(min(min(df['actual']), min(df['position'])) - 50, max(max(df['actual']), max(df['position'])) + 50), clamp=True)
    
    # plot a line chart for stock positions
    actual = alt.Chart(df).mark_line(
        color='green',
        opacity=0.5
    ).encode(
        x='date:T',
        y=alt.Y('position', axis=alt.Axis(format='$.2f', title='Price'), scale=scale)
    ).interactive(
        bind_y=False
    )
    
    # plot the BUY and SELL actions as points
    points = alt.Chart(df).transform_filter(
        alt.datum.action != 'HOLD'
    ).mark_point(
        filled=True
    ).encode(
        x=alt.X('date:T', axis=alt.Axis(title='Date')),
        y=alt.Y('position', axis=alt.Axis(format='$.2f', title='Price'), scale=scale),
        color='action'
    ).interactive(bind_y=False)

    # merge the two charts
    chart = alt.layer(actual, points, title=title).properties(height=300, width=1000)
    
    return chart

In [ ]:
chart = visualize(df, history, title=test_stock)
chart